In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

In [2]:
df=pd.read_excel("capitals_2.xlsx")
points=pd.read_excel("temp.xlsx")

In [3]:
df.head()

Country/Territory   Capital  Population  Year % ofcountry'spopulation  \
0          China PR   Beijing    21542000  2010                    1.5%   
1             Japan     Tokyo    13929286  2017                  11.03%   
2            Russia    Moscow    12506468  2011                   8.52%   
3          DR Congo  Kinshasa    11855000  2012                   12.9%   
4         Indonesia   Jakarta    10075310  2011                   3.76%   

    Latitude   Longitude  CountVenue  RadiusRequest  
0  39.906217  116.391276        1100           2000  
1  35.682839  139.759455         700            500  
2  55.479205   37.327330         700          16000  
3  -4.321706   15.312597          34         100000  
4  -6.175394  106.827183         500           2000

In [4]:
points.head()

Capital   Latitude   Longitude  RadiusRequest  Count
0  Beijing  39.906217  116.391276           2000    100
1  Beijing  39.906217  116.355344           2000     69
2  Beijing  39.906217  116.427207           2000    100
3  Beijing  39.870285  116.391276           2000     46
4  Beijing  39.942149  116.391276           2000    100

In [5]:
with open("Foursquare.txt","r") as file1:
    CLIENT_ID = file1.readline()
    CLIENT_ID = CLIENT_ID[:(-1)] #delete "/n" from readline
    CLIENT_SECRET = file1.readline()
VERSION = "20200101"
LIMIT=100

In [6]:
def getNearbyVenues(names, latitudes, longitudes, radiuses):
    
    venues_list=[]
    for name, lat, lng, radius in zip(names, latitudes, longitudes, radiuses):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        lat, 
        lng, 
        radius, 
        LIMIT)
            
        # make the GET request        
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
            
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Capital', 
                  'Capital Latitude', 
                  'Capital Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [7]:
capital_venues = getNearbyVenues(names=points['Capital'],
                                   latitudes=points['Latitude'],
                                   longitudes=points['Longitude'],
                                   radiuses=points["RadiusRequest"]
                                  )

Beijing
Beijing
Beijing
Beijing
Beijing
Beijing
Beijing
Beijing
Beijing
Tokyo
Tokyo
Tokyo
Tokyo
Tokyo
Tokyo
Tokyo
Moscow
Moscow
Moscow
Moscow
Moscow
Moscow
Moscow
Kinshasa
Jakarta
Jakarta
Jakarta
Jakarta
Jakarta
Seoul
Seoul
Seoul
Seoul
Seoul
Cairo
Cairo
Cairo
Cairo
Cairo
Mexico City
Mexico City
Mexico City
Mexico City
Mexico City
Dhaka
London
London
London
London
London
Lima
Lima
Lima
Lima
Lima
Tehran
Tehran
Tehran
Tehran
Tehran
Bangkok
Bangkok
Bangkok
Bangkok
Bangkok
Hanoi
Hanoi
Hanoi
Hanoi
Riyadh
Riyadh
Riyadh
Riyadh
Hong Kong
Hong Kong
Hong Kong
Hong Kong
Bogotá
Bogotá
Bogotá
Bogotá
Baghdad
Santiago
Santiago
Santiago
Santiago
Singapore
Singapore
Singapore
Ankara
Ankara
Ankara
Berlin
Berlin
Damascus
Algiers
Madrid
Madrid
Pyongyang
Kabul
Nairobi
Nairobi
Addis Ababa
Buenos Aires
Buenos Aires
Rome
Rome
Kiev
Kiev
Yaoundé
Taipei
Taipei
Brasília
Brasília
Amman
Amman
Luanda
Pretoria
Pretoria
Paris
Paris
Tashkent
Tashkent
Baku
Baku
Havana
Phnom Penh
Bucharest
Caracas
Brazzaville
Rabat
Manila

In [8]:
print(capital_venues.shape)
capital_venues.head()

(23199, 7)


Capital  Capital Latitude  Capital Longitude  \
0  Beijing         39.906217         116.391276   
1  Beijing         39.906217         116.391276   
2  Beijing         39.906217         116.391276   
3  Beijing         39.906217         116.391276   
4  Beijing         39.906217         116.391276   

                                             Venue  Venue Latitude  \
0                         Tian'anmen Tower (天安门城楼)       39.906562   
1                                               端门       39.908694   
2             Zhongshan Park (Zhongshan Park 中山公园)       39.908765   
3                        Tian'anmen Square (天安门广场)       39.904848   
4  National Centre for the Performing Arts (国家大剧院)       39.903936   

   Venue Longitude         Venue Category  
0       116.391582          Historic Site  
1       116.391192          Historic Site  
2       116.388602                   Park  
3       116.391306                  Plaza  
4       116.383541  Performing Arts Venue

In [9]:
venues_count=capital_venues[["Capital","Venue"]].groupby('Capital').count()
venues_count

Venue
Capital                         
Abu Dhabi                    100
Abuja                         58
Accra                         82
Adamstown                      1
Addis Ababa                   40
Algiers                       65
Alofi                          5
Amman                        199
Amsterdam                    100
Andorra la Vella             100
Ankara                       203
Antananarivo                  41
Apia                          13
Ashgabat                     100
Asmara                         4
Asunción                     100
Athens                       100
Avarua                         7
Baghdad                       67
Baku                         200
Bamako                        17
Bandar Seri Begawan          100
Bangkok                      391
Bangui                         6
Banjul                        31
Basseterre                   100
Beijing                      654
Beirut                       100
Belfast                      100
Belgrade                     100
Belmopan                      70
Berlin                       200
Berne                        100
Bishkek                       98
Bissau                         7
Bogotá                       158
Brades                        95
Brasília                     150
Bratislava                   100
Brazzaville                   34
Bridgetown                   100
Brussels                     100
Bucharest                    100
Budapest                     100
Buenos Aires                 191
Cairo                        290
Canberra                     100
Caracas                      100
Cardiff                      100
Castries                     100
Charlotte Amalie             100
Chişinău                     100
City of San Marino           100
Cockburn Town                 14
Conakry                       13
Copenhagen                   100
Dakar                         75
Damascus                     100
Dhaka                         60
Dili                          29
Djibouti (city)               20
Dodoma                         4
Doha                         100
Douglas                      100
Dublin                       100
Dushanbe                      44
Edinburgh                    100
El Aaiún                       4
Flying Fish Cove               3
Freetown                      11
Funafuti                       5
Gaborone                      49
George Town                   96
Georgetown                    31
Gibraltar                    100
Gitega                        13
Guatemala                     63
Guayaquil                    100
Gustavia                     100
Hagåtña                       89
Hamilton                      55
Hanoi                        270
Harare                        37
Havana                        64
Helsinki                     100
Hong Kong                    310
Honiara                        4
Islamabad                     33
Jakarta                      500
Jamestown                      3
Jerusalem                    100
Juba                           7
Kabul                         24
Kampala                       85
Kathmandu                     69
Khartoum                      76
Kiev                         171
Kigali                        51
King Edward Point              3
Kingston                     184
Kingstown                     91
Kinshasa                      34
Kuala Lumpur                 100
Kuwait City                  100
Libreville                    22
Lilongwe                      19
Lima                         395
Lisbon                       100
Ljubljana                    100
Lomé                          20
London                       482
Longyearbyen                  23
Luanda                        70
Lusaka                        46
Luxembourg                   100
Macau                        100
Madrid                       200
Majuro                         4
Malabo                         8
Malé                           5
M

In [10]:
for cap in venues_count.index:
    df.loc[df["Capital"]==cap,"CountVenue"]=venues_count.loc[cap,"Venue"]
df.head()

Country/Territory   Capital  Population  Year % ofcountry'spopulation  \
0          China PR   Beijing    21542000  2010                    1.5%   
1             Japan     Tokyo    13929286  2017                  11.03%   
2            Russia    Moscow    12506468  2011                   8.52%   
3          DR Congo  Kinshasa    11855000  2012                   12.9%   
4         Indonesia   Jakarta    10075310  2011                   3.76%   

    Latitude   Longitude  CountVenue  RadiusRequest  
0  39.906217  116.391276         654           2000  
1  35.682839  139.759455         569            500  
2  55.479205   37.327330         572          16000  
3  -4.321706   15.312597          34         100000  
4  -6.175394  106.827183         500           2000

In [11]:
print('There are {} uniques categories.'.format(len(capital_venues['Venue Category'].unique())))

There are 604 uniques categories.


In [12]:
# one hot encoding
capital_onehot = pd.get_dummies(capital_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
capital_onehot['Capital'] = capital_venues['Capital'] 

# move neighborhood column to the first column
fixed_columns = [capital_onehot.columns[-1]] + list(capital_onehot.columns[:-1])
capital_onehot = capital_onehot[fixed_columns]

capital_onehot.head()

Capital  ATM  Acai House  Accessories Store  Acehnese Restaurant  \
0  Beijing    0           0                  0                    0   
1  Beijing    0           0                  0                    0   
2  Beijing    0           0                  0                    0   
3  Beijing    0           0                  0                    0   
4  Beijing    0           0                  0                    0   

   Adult Boutique  Advertising Agency  Afghan Restaurant  African Restaurant  \
0               0                   0                  0                   0   
1               0                   0                  0                   0   
2               0                   0                  0                   0   
3               0                   0                  0                   0   
4               0                   0                  0                   0   

   Airport  Airport Food Court  Airport Lounge  Airport Service  \
0        0                   0               0                0   
1        0                   0               0                0   
2        0                   0               0                0   
3        0                   0               0                0   
4        0                   0               0                0   

   Airport Terminal  Alsatian Restaurant  American Restaurant  Amphitheater  \
0                 0                    0                    0             0   
1                 0                    0                    0             0   
2                 0                    0                    0             0   
3                 0                    0                    0             0   
4                 0                    0                    0             0   

   Antique Shop  Apres Ski Bar  Aquarium  Arcade  Arepa Restaurant  \
0             0              0         0       0                 0   
1             0              0         0       0                 0   
2             0              0         0       0                 0   
3             0              0         0       0                 0   
4             0              0         0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Ash and Haleem Place  Asian Restaurant  \
0                     0                     0                 0   
1                     0                     0                 0   
2                     0                     0                 0   
3                     0                     0                 0   
4                     0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Auto Workshop  Automotive Shop  Auvergne Restaurant  \
0            0              0                0                    0   
1            0              0                0                    0   
2            0              0                0                    0   
3            0              0                0                    0   
4            0              0                0                    0   

   BBQ Joint  Baby Store  Ba

In [13]:
capital_onehot.shape

(23199, 605)

In [14]:
capital_grouped = capital_onehot.groupby('Capital').mean().reset_index()
capital_grouped

Capital   ATM  Acai House  Accessories Store  \
0                    Abu Dhabi  0.00        0.00           0.000000   
1                        Abuja  0.00        0.00           0.000000   
2                        Accra  0.00        0.00           0.000000   
3                    Adamstown  0.00        0.00           0.000000   
4                  Addis Ababa  0.00        0.00           0.000000   
5                      Algiers  0.00        0.00           0.000000   
6                        Alofi  0.00        0.00           0.000000   
7                        Amman  0.00        0.00           0.000000   
8                    Amsterdam  0.00        0.00           0.000000   
9             Andorra la Vella  0.00        0.00           0.000000   
10                      Ankara  0.00        0.00           0.000000   
11                Antananarivo  0.00        0.00           0.000000   
12                        Apia  0.00        0.00           0.000000   
13                    Ashgabat  0.00        0.00           0.000000   
14                      Asmara  0.00        0.00           0.000000   
15                    Asunción  0.00        0.00           0.000000   
16                      Athens  0.00        0.00           0.000000   
17                      Avarua  0.00        0.00           0.000000   
18                     Baghdad  0.00        0.00           0.000000   
19                        Baku  0.00        0.00           0.000000   
20                      Bamako  0.00        0.00           0.000000   
21         Bandar Seri Begawan  0.00        0.00           0.000000   
22                     Bangkok  0.00        0.00           0.000000   
23                      Bangui  0.00        0.00           0.000000   
24                      Banjul  0.00        0.00           0.000000   
25                  Basseterre  0.00        0.00           0.000000   
26                     Beijing  0.00        0.00           0.000000   
27                      Beirut  0.00        0.00           0.010000   
28                     Belfast  0.00        0.00           0.000000   
29                    Belgrade  0.00        0.00           0.000000   
30                    Belmopan  0.00        0.00           0.000000   
31                      Berlin  0.00        0.00           0.000000   
32                       Berne  0.00        0.00           0.000000   
33                     Bishkek  0.00        0.00           0.000000   
34                      Bissau  0.00        0.00           0.000000   
35                      Bogotá  0.00        0.00           0.000000   
36                      Brades  0.00        0.00           0.000000   
37                    Brasília  0.00        0.00           0.013333   
38                  Bratislava  0.00        0.00           0.000000   
39                 Brazzaville  0.00        0.00           0.000000   
40                  Bridgetown  0.00        0.00           0.000000   
41                    Brussels  0.00        0.00           0.000000   
42                   Bucharest  0.00        0.00           0.000000   
43                    Budapest  0.00        0.00           0.000000   
44                Buenos Aires  0.00        0.00           0.000000   
45                       Cairo  0.00        0.00           0.000000   
46                    Canberra  0.00        0.00           0.000000   
47                     Caracas  0.00        0.00           0.000000   
48                     Cardiff  0.00        0.00           0.000000   
49                    Castries  0.00        0.00           0.000000   
50            Charlotte Amalie  0.00        0.00           0.000000   
51                    Chişinău  0.00        0.00           0.000000   
52          City of San Marino  0.00        0.00           0.000000   
53               Cockburn Town  0.00        0.00           0.000000   
54                     Conakry  0.00        0.00           0.000000   
55                  Copenhagen  0.00        0.0

In [78]:
capital_grouped.to_excel("capital_grouped.xlsx")

In [15]:
capital_grouped.shape

(242, 605)

In [16]:
num_top_venues = 5

for hood in capital_grouped['Capital']:
    print("----"+hood+"----")
    temp = capital_grouped[capital_grouped['Capital'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Abu Dhabi----
                  venue  freq
0                  Café  0.10
1           Coffee Shop  0.07
2            Restaurant  0.05
3  Fast Food Restaurant  0.05
4                 Hotel  0.04


----Abuja----
                  venue  freq
0                 Hotel  0.07
1         Shopping Mall  0.07
2  Fast Food Restaurant  0.07
3     Indian Restaurant  0.05
4            Restaurant  0.03


----Accra----
                venue  freq
0               Hotel  0.13
1       Shopping Mall  0.07
2              Resort  0.05
3  African Restaurant  0.05
4        Cocktail Bar  0.04


----Adamstown----
                   venue  freq
0        Nature Preserve   1.0
1                    ATM   0.0
2  Performing Arts Venue   0.0
3                Parking   0.0
4             Pastelaria   0.0


----Addis Ababa----
                  venue  freq
0                 Hotel  0.22
1    Italian Restaurant  0.12
2  Ethiopian Restaurant  0.10
3                  Café  0.08
4            Restaurant  0.08


----Algiers-

4      Lounge  0.05


----Dodoma----
                 venue  freq
0                Hotel  0.50
1          Pizza Place  0.25
2  Rental Car Location  0.25
3                  ATM  0.00
4        Pelmeni House  0.00


----Doha----
                       venue  freq
0                      Hotel  0.12
1                       Café  0.09
2  Middle Eastern Restaurant  0.08
3                Coffee Shop  0.04
4                 Restaurant  0.04


----Douglas----
         venue  freq
0   Restaurant  0.10
1          Pub  0.06
2          Bar  0.06
3  Coffee Shop  0.05
4         Park  0.05


----Dublin----
            venue  freq
0             Pub  0.17
1     Coffee Shop  0.10
2            Café  0.07
3  Clothing Store  0.04
4      Restaurant  0.04


----Dushanbe----
                       venue  freq
0                      Hotel  0.18
1                       Café  0.09
2                 Restaurant  0.07
3           Department Store  0.05
4  Middle Eastern Restaurant  0.05


----Edinburgh----
        ve

4  Fried Chicken Joint  0.04


----Lisbon----
                   venue  freq
0  Portuguese Restaurant  0.14
1                  Plaza  0.08
2             Restaurant  0.05
3                  Hotel  0.05
4               Wine Bar  0.04


----Ljubljana----
         venue  freq
0   Restaurant  0.07
1        Plaza  0.05
2  Pizza Place  0.05
3        Hotel  0.05
4         Café  0.05


----Lomé----
                venue  freq
0               Hotel  0.25
1          Restaurant  0.10
2              Bakery  0.05
3  Spanish Restaurant  0.05
4       Grocery Store  0.05


----London----
            venue  freq
0         Theater  0.06
1           Hotel  0.05
2     Coffee Shop  0.04
3  Sandwich Place  0.03
4      Restaurant  0.03


----Longyearbyen----
            venue  freq
0           Hotel  0.26
1             Bar  0.17
2  Boarding House  0.04
3      Restaurant  0.04
4            Café  0.04


----Luanda----
         venue  freq
0   Restaurant  0.23
1        Beach  0.09
2  Pizza Place  0.07
3        H

4  Eastern European Restaurant  0.04


----Pyongyang----
     venue  freq
0    Hotel  0.50
1  Stadium  0.17
2    Plaza  0.17
3  Airport  0.17
4      ATM  0.00


----Rabat----
                 venue  freq
0                 Café  0.20
1                Hotel  0.11
2  Moroccan Restaurant  0.07
3    French Restaurant  0.06
4          Coffee Shop  0.06


----Ramallah----
                       venue  freq
0                       Café  0.14
1                      Hotel  0.10
2  Middle Eastern Restaurant  0.08
3                Coffee Shop  0.06
4              Historic Site  0.05


----Reykjavík----
                venue  freq
0                 Bar  0.12
1  Seafood Restaurant  0.07
2               Hotel  0.06
3         Coffee Shop  0.05
4        Burger Joint  0.04


----Riga----
                         venue  freq
0  Eastern European Restaurant  0.08
1                        Hotel  0.06
2                          Bar  0.06
3                   Restaurant  0.06
4                        Plaza  0.

4         Pool  0.04


----Tokyo----
                 venue  freq
0  Japanese Restaurant  0.05
1                 Café  0.05
2     Ramen Restaurant  0.04
3          Coffee Shop  0.04
4        Historic Site  0.04


----Tripoli----
                venue  freq
0                Café  0.28
1  Italian Restaurant  0.13
2         Coffee Shop  0.08
3              Bakery  0.05
4               Plaza  0.05


----Tunis----
            venue  freq
0            Café  0.26
1           Hotel  0.23
2  Scenic Lookout  0.08
3     Pizza Place  0.03
4        Tea Room  0.03


----Tórshavn----
                     venue  freq
0                     Café  0.12
1                    Hotel  0.12
2  Scandinavian Restaurant  0.10
3               Lighthouse  0.07
4               Steakhouse  0.05


----Ulaanbaatar----
                  venue  freq
0           Coffee Shop  0.16
1                 Hotel  0.13
2            Soup Place  0.03
3  Fast Food Restaurant  0.03
4   Japanese Restaurant  0.03


----Vaduz----
        

In [17]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [18]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Capital']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

In [19]:


# create a new dataframe
capitals_venues_sorted = pd.DataFrame(columns=columns)
capitals_venues_sorted['Capital'] = capital_grouped['Capital']

for ind in np.arange(capital_grouped.shape[0]):
    capitals_venues_sorted.iloc[ind, 1:] = return_most_common_venues(capital_grouped.iloc[ind, :], num_top_venues)

capitals_venues_sorted.head()

Capital 1st Most Common Venue 2nd Most Common Venue  \
0    Abu Dhabi                  Café           Coffee Shop   
1        Abuja                 Hotel         Shopping Mall   
2        Accra                 Hotel         Shopping Mall   
3    Adamstown       Nature Preserve           Zoo Exhibit   
4  Addis Ababa                 Hotel    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Restaurant  Fast Food Restaurant                 Hotel   
1  Fast Food Restaurant     Indian Restaurant         Movie Theater   
2                Resort    African Restaurant          Cocktail Bar   
3    Falafel Restaurant     Fish & Chips Shop   Filipino Restaurant   
4  Ethiopian Restaurant                  Café            Restaurant   

  6th Most Common Venue       7th Most Common Venue 8th Most Common Venue  \
0    Italian Restaurant                 Pizza Place     Indian Restaurant   
1    Chinese Restaurant                      Arcade       Bed & Breakfast   
2                  Café  Modern European Restaurant         Movie Theater   
3                 Field        Fast Food Restaurant        Farmers Market   
4           Pizza Place                   Nightclub   American Restaurant   

  9th Most Common Venue     10th Most Common Venue  
0                   Spa                        Bar  
1      Department Store             Ice Cream Shop  
2           Pizza Place           Department Store  
3                  Farm                       Fair  
4           Coffee Shop  Middle Eastern Restaurant

In [20]:
# set number of clusters
kclusters = 5

capital_grouped_clustering = capital_grouped.drop('Capital', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(capital_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 3, 3, 4, 3, 3, 1, 3, 3, 3])

In [21]:
# add clustering labels
capitals_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

capital_merged = df

capital_merged.head()

Country/Territory   Capital  Population  Year % ofcountry'spopulation  \
0          China PR   Beijing    21542000  2010                    1.5%   
1             Japan     Tokyo    13929286  2017                  11.03%   
2            Russia    Moscow    12506468  2011                   8.52%   
3          DR Congo  Kinshasa    11855000  2012                   12.9%   
4         Indonesia   Jakarta    10075310  2011                   3.76%   

    Latitude   Longitude  CountVenue  RadiusRequest  
0  39.906217  116.391276         654           2000  
1  35.682839  139.759455         569            500  
2  55.479205   37.327330         572          16000  
3  -4.321706   15.312597          34         100000  
4  -6.175394  106.827183         500           2000

In [22]:
capital_merged.shape

(243, 9)

In [23]:
capitals_venues_sorted.shape

(242, 12)

In [24]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
capital_merged = capital_merged.join(capitals_venues_sorted.set_index('Capital'), on='Capital')

capital_merged.head() # check the last columns!

Country/Territory   Capital  Population  Year % ofcountry'spopulation  \
0          China PR   Beijing    21542000  2010                    1.5%   
1             Japan     Tokyo    13929286  2017                  11.03%   
2            Russia    Moscow    12506468  2011                   8.52%   
3          DR Congo  Kinshasa    11855000  2012                   12.9%   
4         Indonesia   Jakarta    10075310  2011                   3.76%   

    Latitude   Longitude  CountVenue  RadiusRequest  Cluster Labels  \
0  39.906217  116.391276         654           2000               3   
1  35.682839  139.759455         569            500               3   
2  55.479205   37.327330         572          16000               3   
3  -4.321706   15.312597          34         100000               3   
4  -6.175394  106.827183         500           2000               3   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                 Hotel           Coffee Shop    Chinese Restaurant   
1                  Café   Japanese Restaurant         Historic Site   
2                  Park  Gym / Fitness Center            Restaurant   
3                 Hotel                  Café            Restaurant   
4           Coffee Shop                 Hotel    Chinese Restaurant   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Historic Site  Fast Food Restaurant                  Café   
1            Coffee Shop      Ramen Restaurant              Sake Bar   
2            Supermarket                 Hotel           Coffee Shop   
3   Fast Food Restaurant                Lounge                 Diner   
4  Indonesian Restaurant          Noodle House      Asian Restaurant   

  7th Most Common Venue 8th Most Common Venue      9th Most Common Venue  \
0           Pizza Place                   Bar              Shopping Mall   
1     Convenience Store    Chinese Restaurant  Japanese Curry Restaurant   
2           Yoga Studio                  Café                     Resort   
3          Cocktail Bar                  Pool                      Plaza   
4    Seafood Restaurant                  Café       Fast Food Restaurant   

  10th Most Common Venue  
0                   Park  
1     Italian Restaurant  
2          Historic Site  
3            Pizza Place  
4            Pizza Place

In [25]:
print(capital_merged[["Capital","Cluster Labels"]].groupby("Cluster Labels").count(),"\n")

                Capital
Cluster Labels         
0                    33
1                     6
2                    29
3                   174
4                     1 



In [26]:
def Klastering(kclusters):
    # create a new dataframe
    capitals_venues_sorted = pd.DataFrame(columns=columns)
    capitals_venues_sorted['Capital'] = capital_grouped['Capital']

    for ind in np.arange(capital_grouped.shape[0]):
        capitals_venues_sorted.iloc[ind, 1:] = return_most_common_venues(capital_grouped.iloc[ind, :], num_top_venues)

    capital_grouped_clustering = capital_grouped.drop('Capital', 1)

    # run k-means clustering
    kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(capital_grouped_clustering)
    
    # add clustering labels
    capitals_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

    capital_merged = df
    
    # merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
    capital_merged = capital_merged.join(capitals_venues_sorted.set_index('Capital'), on='Capital')
    
    return capital_merged

In [27]:
for k in range(3,25):
    capital_merged = Klastering(k)
    print("For {} number of clusters:".format(k))
    print(capital_merged[["Capital","Cluster Labels"]].groupby("Cluster Labels").count(),"\n")

For 3 number of clusters:
                Capital
Cluster Labels         
0                     4
1                   210
2                    29 

For 4 number of clusters:
                Capital
Cluster Labels         
0                    48
1                     9
2                     1
3                   185 

For 5 number of clusters:
                Capital
Cluster Labels         
0                    33
1                     6
2                    29
3                   174
4                     1 

For 6 number of clusters:
                Capital
Cluster Labels         
0                    47
1                     3
2                     1
3                    38
4                   143
5                    11 

For 7 number of clusters:
                Capital
Cluster Labels         
0                    35
1                   133
2                    15
3                    53
4                     1
5                     1
6                     5 

For 8 number of clus

In [28]:
kclusters = 22
capital_merged = Klastering(kclusters)
print(capital_merged[["Capital","Cluster Labels"]].groupby("Cluster Labels").count(),"\n")

                Capital
Cluster Labels         
0                     7
1                    11
2                    29
3                    44
4                     1
5                     2
6                     3
7                     7
8                    29
9                    31
10                   27
11                    1
12                    1
13                    1
14                    9
15                    1
16                    1
17                    1
18                    1
19                    1
20                   34
21                    1 



In [29]:
# create map
map_clusters = folium.Map()

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(capital_merged['Latitude'], capital_merged['Longitude'], capital_merged['Capital'], capital_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [79]:
capital_merged.set_index("Capital",inplace=True)
capital_merged.head()

Country/Territory  Population  Year % ofcountry'spopulation  \
Capital                                                                
Beijing           China PR    21542000  2010                    1.5%   
Tokyo                Japan    13929286  2017                  11.03%   
Moscow              Russia    12506468  2011                   8.52%   
Kinshasa          DR Congo    11855000  2012                   12.9%   
Jakarta          Indonesia    10075310  2011                   3.76%   

           Latitude   Longitude  CountVenue  RadiusRequest  Cluster Labels  \
Capital                                                                      
Beijing   39.906217  116.391276         654           2000              20   
Tokyo     35.682839  139.759455         569            500               9   
Moscow    55.479205   37.327330         572          16000               9   
Kinshasa  -4.321706   15.312597          34         100000               3   
Jakarta   -6.175394  106.827183         500           2000              20   

         1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
Capital                                                                      
Beijing                  Hotel           Coffee Shop    Chinese Restaurant   
Tokyo                     Café   Japanese Restaurant         Historic Site   
Moscow                    Park  Gym / Fitness Center            Restaurant   
Kinshasa                 Hotel                  Café            Restaurant   
Jakarta            Coffee Shop                 Hotel    Chinese Restaurant   

          4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
Capital                                                                       
Beijing           Historic Site  Fast Food Restaurant                  Café   
Tokyo               Coffee Shop      Ramen Restaurant              Sake Bar   
Moscow              Supermarket                 Hotel           Coffee Shop   
Kinshasa   Fast Food Restaurant                Lounge                 Diner   
Jakarta   Indonesian Restaurant          Noodle House      Asian Restaurant   

         7th Most Common Venue 8th Most Common Venue  \
Capital                                                
Beijing            Pizza Place                   Bar   
Tokyo        Convenience Store    Chinese Restaurant   
Moscow             Yoga Studio                  Café   
Kinshasa          Cocktail Bar                  Pool   
Jakarta     Seafood Restaurant                  Café   

              9th Most Common Venue 10th Most Common Venue  
Capital                                                     
Beijing               Shopping Mall                   Park  
Tokyo     Japanese Curry Restaurant     Italian Restaurant  
Moscow                       Resort          Historic Site  
Kinshasa                      Plaza            Pizza Place  
Jakarta        Fast Food Restaurant            Pizza Place

In [81]:
capital_merged.loc[capital_merged['Cluster Labels'] == 0, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  Longitude  \
Capital                                                                  
Rome                           Italy     2868104  41.893320  12.482932   
Niamey                         Niger      794814  13.524834   2.109823   
Libreville                     Gabon      556425   0.390002   9.454001   
Brussels                     Belgium      148873  50.843671   4.367437   
Monaco                        Monaco       35986  43.732349   7.427683   
City of San Marino        San Marino        4493  43.936400  12.446699   
Vatican City            Vatican City         826  41.903815  12.453153   

                    CountVenue  Cluster Labels 1st Most Common Venue  \
Capital                                                                
Rome                       200               0    Italian Restaurant   
Niamey                      18               0                 Hotel   
Libreville                  22               0                Bakery   
Brussels                   100               0    Italian Restaurant   
Monaco                     100               0    Italian Restaurant   
City of San Marino         100               0    Italian Restaurant   
Vatican City               100               0    Italian Restaurant   

                   2nd Most Common Venue 3rd Most Common Venue  \
Capital                                                          
Rome                               Plaza         Historic Site   
Niamey                Italian Restaurant               Airport   
Libreville            Italian Restaurant                 Hotel   
Brussels                     Coffee Shop        Sandwich Place   
Monaco                             Hotel     French Restaurant   
City of San Marino                 Hotel            Restaurant   
Vatican City              Ice Cream Shop           Pizza Place   

                   4th Most Common Venue 5th Most Common Venue  \
Capital                                                          
Rome                         Pizza Place                 Hotel   
Niamey                            Museum  Fast Food Restaurant   
Libreville                    Restaurant                 Beach   
Brussels                           Hotel            Art Museum   
Monaco                            Garden            Restaurant   
City of San Marino                  Café           Coffee Shop   
Vatican City              Sandwich Place                 Hotel   

                   6th Most Common Venue 7th Most Common Venue  \
Capital                                                          
Rome                      Ice Cream Shop        Sandwich Place   
Niamey                    Soccer Stadium           Fabric Shop   
Libreville            Seafood Restaurant     French Restaurant   
Brussels                            Café                 Plaza   
Monaco                               Spa                   Bar   
City of San Marino                   Bar    Romagna Restaurant   
Vatican City                      Museum           Art Gallery   

                        8th Most Common Venue 9th Most Common Venue  \
Capital                                                               
Rome                                   Bakery            Restaurant   
Niamey              Middle Eastern Restaurant    Turkish Restaurant   
Libreville                     Soccer Stadium           Pizza Place   
Brussels                         Concert Hall          Cocktail Bar   
Monaco                                  Beach      Asian Restaurant   
City of San Marino                Pizza Place                Castle   
Vatican City                       Restaurant                 Plaza   

                   10th Most Common Venue  
Capital                                    
Rome                                  Pub  
Niamey                 African Restaurant  
Libreville                  Shopping Mall  
Brussels             Gym / Fitness Center  
Monaco        

In [82]:
capital_merged.loc[capital_merged['Cluster Labels'] == 1, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude   Longitude  \
Capital                                                              
Bamako                     Mali     1289626  12.605033   -7.986514   
Monrovia                Liberia     1010970   6.328034  -10.797788   
Ouagadougou        Burkina Faso     1005231  12.368148   -1.527085   
Lomé                       Togo      824738   6.130419    1.215829   
N'Djamena                  Chad      751288  12.119154   15.050276   
Bissau            Guinea-Bissau      452640  11.861324  -15.583055   
Port Moresby   Papua New Guinea      299396  -9.474330  147.159950   
Gitega                  Burundi       41944  -3.428495   29.924972   
Banjul               The Gambia       34828  13.441346  -16.562471   
Majuro         Marshall Islands       25400   7.090992  171.381635   
Longyearbyen  Svalbard (Norway)        2075  78.223156   15.646366   

              CountVenue  Cluster Labels 1st Most Common Venue  \
Capital                                                          
Bamako                17               1                 Hotel   
Monrovia              22               1                 Hotel   
Ouagadougou           11               1                 Hotel   
Lomé                  20               1                 Hotel   
N'Djamena             12               1                 Hotel   
Bissau                 7               1                 Hotel   
Port Moresby          14               1                 Hotel   
Gitega                13               1                 Hotel   
Banjul                31               1                 Hotel   
Majuro                 4               1                   Bar   
Longyearbyen          23               1                 Hotel   

             2nd Most Common Venue 3rd Most Common Venue  \
Capital                                                    
Bamako                 Pizza Place               Airport   
Monrovia                   Airport            Restaurant   
Ouagadougou    Lebanese Restaurant    African Restaurant   
Lomé                    Restaurant               Airport   
N'Djamena        French Restaurant    African Restaurant   
Bissau                      Bakery            Restaurant   
Port Moresby                Market       Harbor / Marina   
Gitega                  Restaurant           Pizza Place   
Banjul                      Resort                 River   
Majuro                   Hotel Bar                 Hotel   
Longyearbyen                   Bar               Airport   

                4th Most Common Venue 5th Most Common Venue  \
Capital                                                       
Bamako               Greek Restaurant                Hostel   
Monrovia                Boat or Ferry         Grocery Store   
Ouagadougou                      Pool             Nightclub   
Lomé                            Diner    Spanish Restaurant   
N'Djamena                     Airport                Resort   
Bissau                        Airport                 Plaza   
Port Moresby         Asian Restaurant      Department Store   
Gitega                          Diner                  Café   
Banjul                     Restaurant       Nature Preserve   
Majuro                        Airport           Zoo Exhibit   
Longyearbyen  Scandinavian Restaurant        Boarding House   

             6th Most Common Venue 7th Most Common Venue  \
Capital                                                    
Bamako               Grocery Store           Sports Club   
Monrovia                      Café               Stadium   
Ouagadougou                Airport           Coffee Shop   
Lomé                 Grocery Store  Fast Food Restaurant   
N'Djamena               Hotel Pool                Market   
Bissau                        Fair   Filipino Restaurant   
Port Moresby         Shopping Mall    Chinese Restaurant   
Gitega                      Bistro    African Restaurant   
Banjul                         Pub         

In [83]:
capital_merged.loc[capital_merged['Cluster Labels'] == 2, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  \
Capital                                                               
Cairo                                  Egypt     9500000  30.048819   
Dhaka                             Bangladesh     8906039  23.759357   
Tehran                                  Iran     8693706  35.700618   
Amman                                 Jordan     2600603  31.951569   
Pretoria                        South Africa     2345908 -25.745937   
Baku                              Azerbaijan     2204200  40.375443   
Rabat                                Morocco     1789635  34.022405   
Warsaw                                Poland     1711324  52.233717   
Harare                              Zimbabwe     1487028 -17.831773   
Tripoli                                Libya     1184045  32.896672   
Kuwait City                           Kuwait     1171880  29.379709   
Tbilisi                              Georgia     1044993  41.693459   
Tegucigalpa                         Honduras      735982  14.077386   
Abu Dhabi               United Arab Emirates      585097  24.396474   
Bratislava                          Slovakia      424207  48.151699   
Canberra                           Australia      410301 -35.297591   
Sarajevo              Bosnia and Herzegovina      395133  43.851977   
Nicosia (south)                       Cyprus      270000  35.173930   
New Delhi                              India      142004  28.614179   
Manama                               Bahrain      140616  26.223504   
Nicosia                      Northern Cyprus       84893  35.173930   
Suva                                    Fiji       84410 -18.141588   
Tarawa                              Kiribati       30000  11.588415   
Bandar Seri Begawan                   Brunei       28135   4.889545   
Ramallah                           Palestine       25500  31.903082   
Tórshavn             Faroe Islands (Denmark)       18573  62.012000   
Mariehamn                    Åland (Finland)       11296  60.102423   
Avarua                     Cook Islands (NZ)        5445 -21.207474   
Alofi                              Niue (NZ)         616 -19.053416   

                      Longitude  CountVenue  Cluster Labels  \
Capital                                                       
Cairo                 31.243666         290               2   
Dhaka                 90.378814          60               2   
Tehran                51.401378         391               2   
Amman                 35.923963         199               2   
Pretoria              28.187944         137               2   
Baku                  49.832675         200               2   
Rabat                 -6.834543         100               2   
Warsaw                21.071411         100               2   
Harare                31.045686          37               2   
Tripoli               13.177792          39               2   
Kuwait City           47.973563         100               2   
Tbilisi               44.801449         100               2   
Tegucigalpa          -87.195419         100               2   
Abu Dhabi             54.536663         100               2   
Bratislava            17.109306         100               2   
Canberra             149.101268         100               2   
Sarajevo              18.386687         100               2   
Nicosia (south)       33.364726         100               2   
New Delhi             77.202266         100               2   
Manama                50.582244         100               2   
Nicosia               33.364726         100               2   
Suva                 178.442166          49               2   
Tarawa                 3.970774           9               2   
Bandar Seri Begawan  114.941757         100               2   
Ramallah              35.195174         100               2   
Tórshavn              -6.768000          42               2   
Mariehamn             19.941260          74               2  

In [84]:
capital_merged.loc[capital_merged['Cluster Labels'] == 3, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  \
Capital                                                                      
Kinshasa                                   DR Congo    11855000  -4.321706   
Baghdad                                        Iraq     6719500  33.302431   
Algiers                                     Algeria     3415811  36.775361   
Kabul                                   Afghanistan     3140853  34.526013   
Addis Ababa                                Ethiopia     3040740   9.010793   
Yaoundé                                    Cameroon     2765568   3.868987   
Havana                                         Cuba     2135498  23.135305   
Phnom Penh                                 Cambodia     2011725  11.568271   
Brazzaville                                   Congo     1827000  -4.269441   
Accra                                         Ghana     1640507   5.560014   
Antananarivo                             Madagascar     1613375 -18.910012   
Doha                                          Qatar     1450000  25.285633   
Lusaka                                       Zambia     1331254 -15.416449   
Maputo                                   Mozambique     1076689 -25.966213   
Freetown                               Sierra Leone     1070200   8.479004   
Dakar                                       Senegal     1030594  14.693425   
Nur-Sultan (Astana)                      Kazakhstan     1029556  51.128220   
Guatemala                                 Guatemala     1022000  15.635609   
Islamabad                                  Pakistan      955629  22.330800   
Naypyidaw                                   Myanmar      925000  19.754005   
Lilongwe                                     Malawi      902388 -13.987511   
Panama City                                  Panama      813097   8.971449   
Jerusalem                                    Israel      927000  31.778345   
Kigali                                       Rwanda      718414  -1.885960   
Dushanbe                                 Tajikistan      582496  38.542583   
Edinburgh                             Scotland (UK)      492680  55.953346   
Vientiane                                      Laos      287579  17.964099   
Windhoek                                    Namibia      252721 -22.574392   
Gaborone                                   Botswana      225656 -24.658136   
Tiraspol                               Transnistria      159163  46.837999   
Port Louis                                Mauritius      147251 -20.163728   
Georgetown                                   Guyana      134599   6.802577   
Praia                                    Cape Verde      125464  14.916017   
Mbabane                        Eswatini (Swaziland)       81594 -26.325745   
Luxembourg                               Luxembourg      119214  49.815868   
Saipan               Northern Mariana Islands (USA)       62392  15.190983   
Dili                                     East Timor       59069  -8.553681   
Stepanakert               Nagorno-Karabakh Republic       49986  39.824945   
Apia                                          Samoa       39813 -13.834369   
Saint Helier                            Jersey (UK)       28380  47.384387   
Andorra la Vella                            Andorra       22884  42.506939   
St. Peter Port                        Guernsey (UK)       16701  49.456814   
Vaduz                                 Liechtenstein        5248  47.139286   
Hagåtña                                   Guam (US)        1100  13.472745   

                      Longitude  CountVenue  Cluster Labels  \
Capital                                                       
Kinshasa              15.312597          34               3   
Baghdad               44.378799          67               3   
Algiers                3.060188          65               3   
Kabul                 69.177648          24               3   
Addis Ababa           38.761252          40               3   
Yaou

In [85]:
capital_merged.loc[capital_merged['Cluster Labels'] == 4, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  \
Capital                                                                   
West Island  Cocos (Keeling) Islands (Australia)         120 -12.189848   

             Longitude  CountVenue  Cluster Labels 1st Most Common Venue  \
Capital                                                                    
West Island  96.830449           1               4               Airport   

            2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
Capital                                                                         
West Island    Falafel Restaurant           Fish Market     Fish & Chips Shop   

            5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
Capital                                                                         
West Island   Filipino Restaurant                 Field  Fast Food Restaurant   

            8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
Capital                                                                         
West Island        Farmers Market                  Farm            Zoo Exhibit

In [86]:
capital_merged.loc[capital_merged['Cluster Labels'] == 5, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude   Longitude  \
Capital                                                                      
Asmara                          Eritrea      694000  15.338967   38.932676   
Palikir  Federated States of Micronesia        9900   6.920744  158.162714   

         CountVenue  Cluster Labels 1st Most Common Venue  \
Capital                                                     
Asmara            4               5                 Hotel   
Palikir           4               5                 Hotel   

        2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
Capital                                                                     
Asmara            Zoo Exhibit    Falafel Restaurant     Fish & Chips Shop   
Palikir               Airport           Zoo Exhibit    Falafel Restaurant   

        5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
Capital                                                                     
Asmara    Filipino Restaurant                 Field  Fast Food Restaurant   
Palikir     Fish & Chips Shop   Filipino Restaurant                 Field   

        8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
Capital                                                                     
Asmara         Farmers Market                  Farm                   Fair  
Palikir  Fast Food Restaurant        Farmers Market                   Farm

In [87]:
capital_merged.loc[capital_merged['Cluster Labels'] == 6, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude   Longitude  \
Capital                                                                   
Funafuti                      Tuvalu        4492  -8.534995  179.118650   
Mata-Utu  Wallis and Futuna (France)        1191 -13.282042 -176.174022   
Yaren                          Nauru        1100  -0.547101  166.916400   

          CountVenue  Cluster Labels 1st Most Common Venue  \
Capital                                                      
Funafuti           5               6                 Hotel   
Mata-Utu           2               6                 Hotel   
Yaren              4               6                 Hotel   

         2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
Capital                                                                      
Funafuti       Bed & Breakfast                 Beach               Airport   
Mata-Utu               Airport           Zoo Exhibit    Falafel Restaurant   
Yaren         Department Store               Airport           Zoo Exhibit   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
Capital                                                                      
Funafuti           Zoo Exhibit        Farmers Market     Fish & Chips Shop   
Mata-Utu     Fish & Chips Shop   Filipino Restaurant                 Field   
Yaren                     Farm     Fish & Chips Shop   Filipino Restaurant   

         8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
Capital                                                                      
Funafuti   Filipino Restaurant                 Field   Fast Food Restaurant  
Mata-Utu  Fast Food Restaurant        Farmers Market                   Farm  
Yaren                    Field  Fast Food Restaurant         Farmers Market

In [88]:
capital_merged.loc[capital_merged['Cluster Labels'] == 7, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude   Longitude  \
Capital                                                                  
Kampala                      Uganda     1659600   0.317714   32.581354   
Sana'a                        Yemen     1431649  15.353857   44.205884   
Tunis                       Tunisia      767629  33.843941    9.400138   
Nouakchott               Mauritania      719167  18.079238  -15.978007   
Port Vila                   Vanuatu       38000 -17.741497  168.315016   
Nukuʻalofa                    Tonga       22400 -21.134340 -175.201808   
Nuuk (Godthåb)  Greenland (Denmark)       15469  64.175029  -51.735539   

                CountVenue  Cluster Labels  1st Most Common Venue  \
Capital                                                             
Kampala                 85               7                   Café   
Sana'a                  13               7                   Café   
Tunis                   39               7                   Café   
Nouakchott              18               7                  Hotel   
Port Vila               11               7                 Resort   
Nukuʻalofa               8               7                   Café   
Nuuk (Godthåb)           5               7  General Entertainment   

               2nd Most Common Venue 3rd Most Common Venue  \
Capital                                                      
Kampala                        Hotel           Coffee Shop   
Sana'a                   Coffee Shop                 Hotel   
Tunis                          Hotel        Scenic Lookout   
Nouakchott                      Café            Restaurant   
Port Vila                      Hotel                  Café   
Nukuʻalofa                     Hotel           Fish Market   
Nuuk (Godthåb)                  Café                 Hotel   

                4th Most Common Venue 5th Most Common Venue  \
Capital                                                       
Kampala            African Restaurant                Resort   
Sana'a                     Hookah Bar  Fast Food Restaurant   
Tunis                       BBQ Joint                  Farm   
Nouakchott      Portuguese Restaurant    Turkish Restaurant   
Port Vila           French Restaurant            Restaurant   
Nukuʻalofa              Track Stadium               Airport   
Nuuk (Godthåb)          Shopping Mall               Airport   

                        6th Most Common Venue 7th Most Common Venue  \
Capital                                                               
Kampala                            Restaurant     Indian Restaurant   
Sana'a                      Indian Restaurant         Shopping Mall   
Tunis                             Coffee Shop              Tea Room   
Nouakchott                             Market         Shopping Mall   
Port Vila                         Beer Garden       Harbor / Marina   
Nukuʻalofa      Paper / Office Supplies Store           Event Space   
Nuuk (Godthåb)                           Fair                 Field   

               8th Most Common Venue  9th Most Common Venue  \
Capital                                                       
Kampala                          Bar  Performing Arts Venue   
Sana'a                Airport Lounge                Exhibit   
Tunis                    Beer Garden          Shopping Mall   
Nouakchott       Moroccan Restaurant   Fast Food Restaurant   
Port Vila                Zoo Exhibit     Falafel Restaurant   
Nukuʻalofa                   Exhibit            Fabric Shop   
Nuuk (Godthåb)  Fast Food Restaurant         Farmers Market   

               10th Most Common Venue  
Capital                                
Kampala                   Beer Garden  
Sana'a                    Fabric Shop  
Tunis                  History Museum  
Nouakchott                     Bakery  
Port Vila                       Field  
Nukuʻalofa       Ethiopian Restaurant  
Nuuk (Godthåb)                   Farm

In [89]:
capital_merged.loc[capital_merged['Cluster Labels'] == 8, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude   Longitude  \
Capital                                                                     
Bogotá                        Colombia     7181469   4.598080  -74.076044   
Damascus                         Syria     3500000  33.513070   36.309581   
Madrid                           Spain     3233527  40.416705   -3.703582   
Brasília                        Brazil     2648532 -15.793889  -47.882778   
Luanda                          Angola     2453779  -8.827270   13.243951   
Vienna                         Austria     1749673  48.208354   16.372504   
Montevideo                     Uruguay     1369797 -34.905904  -56.191357   
Prague                  Czech Republic     1241664  50.087465   14.421254   
Belgrade                        Serbia     1154589  44.817813   20.456897   
Yerevan                        Armenia     1080487  40.177612   44.512585   
Kathmandu                        Nepal     1003285  27.708796   85.320244   
Zagreb                         Croatia      804200  45.813177   15.977048   
Tirana                         Albania      763634  41.315886   19.900912   
Ashgabat                  Turkmenistan      763537  37.937832   58.235947   
Riga                            Latvia      713016  56.949398   24.105185   
Lisbon                        Portugal      564657  38.707751   -9.136592   
Skopje                 North Macedonia      521000  41.996092   21.431649   
Djibouti (city)               Djibouti      475332  11.814597   42.845306   
Tallinn                        Estonia      440206  59.437216   24.745369   
Wellington                 New Zealand      405000 -41.288795  174.777211   
Belfast          Northern Ireland (UK)      333871  54.596441   -5.930276   
Ljubljana                     Slovenia      280140  46.049980   14.506860   
Sucre                          Bolivia      261201 -19.047725  -65.259431   
Prishtina                       Kosovo      198214  42.663877   21.164085   
Podgorica                   Montenegro      141854  42.441524   19.262108   
Berne                      Switzerland      121631  46.948271    7.451451   
Gibraltar               Gibraltar (UK)       29286  36.106747   -5.335277   
Douglas               Isle of Man (UK)       26600  54.235817   -4.514599   
Valletta                         Malta        6444  35.898982   14.513676   

                 CountVenue  Cluster Labels        1st Most Common Venue  \
Capital                                                                    
Bogotá                  158               8                   Restaurant   
Damascus                100               8                     Mountain   
Madrid                  200               8                        Hotel   
Brasília                150               8                        Hotel   
Luanda                   70               8                   Restaurant   
Vienna                  100               8                         Café   
Montevideo              100               8                          Bar   
Prague                  100               8                         Café   
Belgrade                100               8                        Hotel   
Yerevan                 100               8                        Hotel   
Kathmandu                69               8                         Café   
Zagreb                  100               8                          Bar   
Tirana                  100               8           Italian Restaurant   
Ashgabat                100               8                   Restaurant   
Riga                    100               8  Eastern European Restaurant   
Lisbon                  100               8        Portuguese Restaurant   
Skopje                  100               8                         Café   
Djibouti (city)          20               8                   Restaurant   
Tallinn                 100               8  Eastern European Restaurant   
Wellington              100          

In [90]:
capital_merged.loc[capital_merged['Cluster Labels'] == 9, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  \
Capital                                                                  
Tokyo                                     Japan    13929286  35.682839   
Moscow                                   Russia    12506468  55.479205   
Mexico City                              Mexico     8918653  19.432630   
Lima                                       Peru     8852000 -12.062107   
Bangkok                                Thailand     8305218  13.754253   
Riyadh                             Saudi Arabia     7676654  24.631969   
Singapore                             Singapore     5638700   1.357107   
Ankara                                   Turkey     5445026  39.716044   
Buenos Aires                          Argentina     2891082 -34.607568   
Taipei                                   Taiwan     2668572  25.037520   
Paris                                    France     2241346  48.856697   
Caracas                               Venezuela     1838939  10.506098   
Manila                              Philippines     1780148  14.590622   
Khartoum                                  Sudan     1840661  15.593325   
Budapest                                Hungary     1729040  47.481390   
Kuala Lumpur                           Malaysia     1381830   3.151696   
Santo Domingo                Dominican Republic     1111838  18.480197   
Stockholm                                Sweden      962154  59.325117   
Managua                               Nicaragua      926883  12.146124   
Muscat                                     Oman      797000  23.599786   
Abuja                                   Nigeria      778567   9.064331   
Helsinki                                Finland      635591  60.167410   
Copenhagen                              Denmark      562253  55.686724   
San Salvador                        El Salvador      521366  13.698994   
Asunción                               Paraguay      520722 -25.280046   
Macau                                     Macau      520400  -5.113366   
Paramaribo                             Suriname      254147   5.821609   
Porto-Novo                                Benin      223552   6.499072   
Sri Jayawardenepura Kotte             Sri Lanka      115826   6.888322   
Malé                                   Maldives      103693  16.370036   
Pago Pago                  American Samoa (USA)       52000 -14.275479   

                            Longitude  CountVenue  Cluster Labels  \
Capital                                                             
Tokyo                      139.759455         569               9   
Moscow                      37.327330         572               9   
Mexico City                -99.133178         325               9   
Lima                       -77.036526         395               9   
Bangkok                    100.493087         391               9   
Riyadh                      46.715065         335               9   
Singapore                  103.819499         291               9   
Ankara                      32.705995         203               9   
Buenos Aires               -58.437089         191               9   
Taipei                     121.563680         173               9   
Paris                        2.351462         200               9   
Caracas                    -66.914602         100               9   
Manila                     120.979970         100               9   
Khartoum                    32.535650          76               9   
Budapest                    19.146073         100               9   
Kuala Lumpur               101.694237         100               9   
Santo Domingo              -69.942111         100               9   
Stockholm                   18.071093         100               9   
Managua                    -86.273717         100               9   
Muscat                      58.545130         100               9   
Abuja                        7.489297          58               9   


In [91]:
capital_merged.loc[capital_merged['Cluster Labels'] == 10, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population  \
Capital                                                               
Port-au-Prince                                    Haiti     1235227   
Kingston                                        Jamaica      701063   
Yamoussoukro                              Côte d'Ivoire      454929   
Nassau                                          Bahamas      248948   
Bridgetown                                     Barbados      110000   
Nouméa                           New Caledonia (France)       89207   
Castries                                    Saint Lucia       70000   
Willemstad                        Curaçao (Netherlands)       49885   
Kingstown              Saint Vincent and the Grenadines       40020   
Oranjestad                          Aruba (Netherlands)       29998   
Victoria                                     Seychelles       29298   
George Town                         Cayman Islands (UK)       26798   
Papeete                       French Polynesia (France)       26200   
St. John's                          Antigua and Barbuda       22679   
Belmopan                                         Belize       16451   
Roseau                                         Dominica       14847   
Basseterre                        Saint Kitts and Nevis       13043   
Charlotte Amalie      United States Virgin Islands (US)       10817   
Road Town                   British Virgin Islands (UK)        9400   
Gustavia                      Saint Barthélemy (France)        6000   
Marigot           Collectivity of Saint Martin (France)        5700   
Cockburn Town             Turks and Caicos Islands (UK)        3700   
Philipsburg                  Sint Maarten (Netherlands)        1338   
The Valley                                Anguilla (UK)        1169   
Hamilton                                   Bermuda (UK)        1010   
Kingston                     Norfolk Island (Australia)         880   
Brades                                  Montserrat (UK)         391   

                   Latitude   Longitude  CountVenue  Cluster Labels  \
Capital                                                               
Port-au-Prince    18.547327  -72.339593          65              10   
Kingston          17.971215  -76.792813         184              10   
Yamoussoukro       6.809107   -5.273263           7              10   
Nassau            25.078346  -77.338333         100              10   
Bridgetown        13.097783  -59.618418         100              10   
Nouméa           -22.274526  166.442419          39              10   
Castries          13.952589  -60.987824         100              10   
Willemstad        12.109124  -68.931655         100              10   
Kingstown         13.156186  -61.227962          91              10   
Oranjestad        12.526874  -70.035685         100              10   
Victoria          -4.623208   55.452359          95              10   
George Town       19.295355  -81.380778          96              10   
Papeete          -17.537384 -149.565996          59              10   
St. John's        17.118457  -61.844851          65              10   
Belmopan          17.250199  -88.770018          70              10   
Roseau            15.299192  -61.387287         100              10   
Basseterre        17.296092  -62.722301         100              10   
Charlotte Amalie  18.341137  -64.932789         100              10   
Road Town         18.425713  -64.623223         100              10   
Gustavia          17.895704  -62.850837         100              10   
Marigot           18.066854  -63.084887         100              10   
Cockburn Town     21.460772  -71.139996          14              10   
Philipsburg       18.025071  -63.048307         100              10   
The Valley        18.214586  -63.051776         100              10   
Hamilton          32.295608  -64.782705          55              10   
Kingston          17.971215  -76.792813         184          

In [92]:
capital_merged.loc[capital_merged['Cluster Labels'] == 11, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population  Latitude  Longitude  CountVenue  \
Capital                                                                     
Jamestown  Saint Helena (UK)         714 -15.92773  -5.716087           3   

           Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
Capital                                                                 
Jamestown              11         Grocery Store    Chinese Restaurant   

          3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
Capital                                                                       
Jamestown         Moving Target     Fish & Chips Shop   Filipino Restaurant   

          6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
Capital                                                                       
Jamestown                 Field  Fast Food Restaurant        Farmers Market   

          9th Most Common Venue 10th Most Common Venue  
Capital                                                 
Jamestown                  Farm     Falafel Restaurant

In [93]:
capital_merged.loc[capital_merged['Cluster Labels'] == 12, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population  Latitude  Longitude  \
Capital                                                              
Bangui   Central African Republic      731548  4.390715  18.550913   

         CountVenue  Cluster Labels 1st Most Common Venue  \
Capital                                                     
Bangui            6              12                  Café   

        2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
Capital                                                                     
Bangui      French Restaurant                 Hotel               Airport   

        5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
Capital                                                                     
Bangui                   Lake       Nature Preserve           Zoo Exhibit   

        8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
Capital                                                                     
Bangui         Farmers Market     Fish & Chips Shop    Filipino Restaurant

In [94]:
capital_merged.loc[capital_merged['Cluster Labels'] == 13, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  Longitude  CountVenue  \
Capital                                                                        
Stanley  Falkland Islands (UK)        2115 -51.695057 -57.849169           5   

         Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
Capital                                                               
Stanley              13               Airport                  Port   

              3rd Most Common Venue 4th Most Common Venue  \
Capital                                                     
Stanley  Tourist Information Center         Grocery Store   

        5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
Capital                                                                     
Stanley           Zoo Exhibit                  Farm     Fish & Chips Shop   

        8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
Capital                                                                     
Stanley   Filipino Restaurant                 Field   Fast Food Restaurant

In [95]:
capital_merged.loc[capital_merged['Cluster Labels'] == 14, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  \
Capital                                                              
Pyongyang                       North Korea     3144005  39.019474   
Conakry                              Guinea     1399981   9.517060   
Juba                            South Sudan      372410   4.847202   
Dodoma                             Tanzania      287200  -6.337282   
El Aaiún   Sahrawi Arab Democratic Republic      194668  27.154512   
Thimphu                              Bhutan      101259  27.472762   
Malabo                    Equatorial Guinea      100677   3.752828   
Moroni                              Comoros       60200 -11.693126   
São Tomé              São Tomé and Príncipe       56166   0.338924   

            Longitude  CountVenue  Cluster Labels 1st Most Common Venue  \
Capital                                                                   
Pyongyang  125.753388           6              14                 Hotel   
Conakry    -13.699843          13              14                 Hotel   
Juba        31.595166           7              14                 Hotel   
Dodoma      35.737177           4              14                 Hotel   
El Aaiún   -13.195392           4              14                 Hotel   
Thimphu     89.629548          50              14                 Hotel   
Malabo       8.780061           8              14                 Hotel   
Moroni      43.254304           8              14                 Hotel   
São Tomé     6.731303           9              14                 Hotel   

          2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
Capital                                                                       
Pyongyang                 Plaza               Stadium               Airport   
Conakry       French Restaurant    Mexican Restaurant     Electronics Store   
Juba              Grocery Store                  Café            Restaurant   
Dodoma              Pizza Place   Rental Car Location           Zoo Exhibit   
El Aaiún                 Resort    African Restaurant                  Fair   
Thimphu                    Café                Resort         Historic Site   
Malabo                     Café     French Restaurant             Hotel Bar   
Moroni                   Resort    Falafel Restaurant        Adult Boutique   
São Tomé                   Café             BBQ Joint                   Bar   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
Capital                                                                       
Pyongyang                  Fair   Filipino Restaurant                 Field   
Conakry      Turkish Restaurant                Resort         Shopping Mall   
Juba              Shopping Mall    Falafel Restaurant                 Field   
Dodoma       Falafel Restaurant   Filipino Restaurant                 Field   
El Aaiún    Filipino Restaurant                 Field  Fast Food Restaurant   
Thimphu        Asian Restaurant   Monument / Landmark                   Pub   
Malabo                    Motel                Resort           Zoo Exhibit   
Moroni            National Park           Fish Market   Filipino Restaurant   
São Tomé                Airport                  Farm     Fish & Chips Shop   

          8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
Capital                                                                       
Pyongyang  Fast Food Restaurant        Farmers Market                   Farm  
Conakry        Pedestrian Plaza           Fabric Shop         Farmers Market  
Juba       Fast Food Restaurant        Farmers Market                   Farm  
Dodoma     Fast Food Restaurant        Farmers Market                   Farm  
El Aaiún         Farmers Market                  Farm     Falafel Restaurant  
Thimphu                Mountain            Restaurant                    Zoo  
Malabo       Falafel Restaurant  Fast Food Restaurant    

In [96]:
capital_merged.loc[capital_merged['Cluster Labels'] == 15, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population  Latitude  Longitude  CountVenue  \
Capital                                                                    
Mogadishu           Somalia     1097133  2.042778  45.338564           8   

           Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
Capital                                                                 
Mogadishu              15       Automotive Shop                 Beach   

          3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
Capital                                                                       
Mogadishu                 Hotel           Zoo Exhibit    Falafel Restaurant   

          6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
Capital                                                                       
Mogadishu   Filipino Restaurant                 Field  Fast Food Restaurant   

          9th Most Common Venue 10th Most Common Venue  
Capital                                                 
Mogadishu        Farmers Market                   Farm

In [97]:
capital_merged.loc[capital_merged['Cluster Labels'] == 16, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  \
Capital                                                                 
Flying Fish Cove  Christmas Island (Australia)        1493 -10.426665   

                   Longitude  CountVenue  Cluster Labels  \
Capital                                                    
Flying Fish Cove  105.668672           3              16   

                 1st Most Common Venue 2nd Most Common Venue  \
Capital                                                        
Flying Fish Cove                 Diner         National Park   

                 3rd Most Common Venue 4th Most Common Venue  \
Capital                                                        
Flying Fish Cove               Airport                  Farm   

                 5th Most Common Venue 6th Most Common Venue  \
Capital                                                        
Flying Fish Cove           Fish Market     Fish & Chips Shop   

                 7th Most Common Venue 8th Most Common Venue  \
Capital                                                        
Flying Fish Cove   Filipino Restaurant                 Field   

                 9th Most Common Venue 10th Most Common Venue  
Capital                                                        
Flying Fish Cove  Fast Food Restaurant         Farmers Market

In [98]:
capital_merged.loc[capital_merged['Cluster Labels'] == 17, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population  Latitude   Longitude  CountVenue  \
Capital                                                                   
Honiara   Solomon Islands       59288 -9.431077  159.955255           4   

         Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
Capital                                                               
Honiara              17                  Café                Resort   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
Capital                                                                     
Honiara               Airport                  Fair   Filipino Restaurant   

        6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
Capital                                                                     
Honiara                 Field  Fast Food Restaurant        Farmers Market   

        9th Most Common Venue 10th Most Common Venue  
Capital                                               
Honiara                  Farm     Falafel Restaurant

In [99]:
capital_merged.loc[capital_merged['Cluster Labels'] == 18, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude   Longitude  \
Capital                                                               
Adamstown  Pitcairn Islands (UK)          56 -25.066667 -130.100205   

           CountVenue  Cluster Labels 1st Most Common Venue  \
Capital                                                       
Adamstown           1              18       Nature Preserve   

          2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
Capital                                                                       
Adamstown           Zoo Exhibit    Falafel Restaurant     Fish & Chips Shop   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
Capital                                                                       
Adamstown   Filipino Restaurant                 Field  Fast Food Restaurant   

          8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
Capital                                                                       
Adamstown        Farmers Market                  Farm                   Fair

In [100]:
capital_merged.loc[capital_merged['Cluster Labels'] == 19, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  \
Capital                                                                
King Edward Point  South Georgia and the South Sandwich Islands (UK)   

                   Population   Latitude  Longitude  CountVenue  \
Capital                                                           
King Edward Point          22 -54.283545 -36.494636           3   

                   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
Capital                                                                         
King Edward Point              19           Observatory             Racetrack   

                  3rd Most Common Venue 4th Most Common Venue  \
Capital                                                         
King Edward Point                   Bay           Zoo Exhibit   

                  5th Most Common Venue 6th Most Common Venue  \
Capital                                                         
King Edward Point                  Farm     Fish & Chips Shop   

                  7th Most Common Venue 8th Most Common Venue  \
Capital                                                         
King Edward Point   Filipino Restaurant                 Field   

                  9th Most Common Venue 10th Most Common Venue  
Capital                                                         
King Edward Point  Fast Food Restaurant         Farmers Market

In [101]:
capital_merged.loc[capital_merged['Cluster Labels'] == 20, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  \
Capital                                                                       
Beijing                                     China PR    21542000  39.906217   
Jakarta                                    Indonesia    10075310  -6.175394   
Seoul                                    South Korea     9838892  37.564983   
London                        United Kingdom England     8908081  51.507322   
Hanoi                                        Vietnam     7781631  21.029450   
Hong Kong                                  Hong Kong     7482500  22.279328   
Santiago                                       Chile     6310000 -33.437797   
Berlin                                       Germany     3748148  52.517037   
Nairobi                                        Kenya     3138369  -1.283253   
Kiev                                         Ukraine     2847200  50.450034   
Tashkent                                  Uzbekistan     2207850  41.312336   
Bucharest                                    Romania     1942254  44.436141   
Minsk                                        Belarus     1702061  53.902334   
Beirut                                       Lebanon     1574387  33.895920   
Guayaquil                                    Ecuador     1504991  -2.189907   
Sofia                                       Bulgaria     1277000  42.697863   
Dublin                                       Ireland     1173179  53.349764   
Ottawa                                        Canada      934243  45.421106   
Ulaanbaatar                                 Mongolia      907802  47.918468   
Amsterdam                                Netherlands      855965  52.372760   
Bishkek                                   Kyrgyzstan      843240  42.876562   
Chişinău                                     Moldova      794800  47.024471   
Athens                                        Greece      664046  37.984149   
Washington, D.C.                       United States      658893  38.894893   
Oslo                                          Norway      645701  59.913330   
Vilnius                                    Lithuania      556723  54.687046   
San Juan                            Puerto Rico (US)      421356  18.465299   
Cardiff                                   Wales (UK)      346100  51.481655   
San José                                  Costa Rica      328195   9.932543   
Reykjavík                                    Iceland      115000  64.145981   
Port of Spain                    Trinidad and Tobago       50479  10.657268   
St. George's                                 Grenada        7500  48.658138   
Saint-Pierre      Saint Pierre and Miquelon (France)        5509  46.783247   
Ngerulmud                                      Palau         391   7.500619   

                   Longitude  CountVenue  Cluster Labels  \
Capital                                                    
Beijing           116.391276         654              20   
Jakarta           106.827183         500              20   
Seoul             126.939211         385              20   
London             -0.127647         482              20   
Hanoi             105.854444         270              20   
Hong Kong         114.162813         310              20   
Santiago          -70.650445         397              20   
Berlin             13.388860         200              20   
Nairobi            36.817245         200              20   
Kiev               30.524136         171              20   
Tashkent           69.278708         153              20   
Bucharest          26.102720         100              20   
Minsk              27.561879         100              20   
Beirut             35.478430         100              20   
Guayaquil         -79.887726         100              20   
Sofia              23.322179         100              20   
Dublin             -6.260273         100              20   
Ottawa            -75.690308         100          

In [102]:
capital_merged.loc[capital_merged['Cluster Labels'] == 21, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Country/Territory  Population   Latitude  Longitude  CountVenue  \
Capital                                                                   
Maseru            Lesotho      267652 -29.310054  27.478222           6   

         Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
Capital                                                               
Maseru               21         Shopping Mall                Casino   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
Capital                                                                     
Maseru                  Hotel            Restaurant                  Fair   

        6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
Capital                                                                     
Maseru                  Field  Fast Food Restaurant        Farmers Market   

        9th Most Common Venue 10th Most Common Venue  
Capital                                               
Maseru                   Farm     Falafel Restaurant

In [103]:
capital_merged.loc[capital_merged['Cluster Labels'] == 22, capital_merged.columns[[0,1,4,5,6] + list(range(8, capital_merged.shape[1]))]]

Empty DataFrame
Columns: [Country/Territory, Population, Latitude, Longitude, CountVenue, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue]
Index: []